In [1]:
import warnings
warnings.filterwarnings("ignore")
import IPython
from IPython.display import display, Markdown
import os
import numpy as np
import pandas as pd
import librosa
import keras

Using TensorFlow backend.


# Let's make a prediction using the Mood Algorithm

#### *...in 3 easy steps!*

## Step 1. Import the Song

In [2]:
def extract_samples(file_name, offset):
    sr = 12000
    segment_length = 31104
    duration = 2.592 # 31104 samples @ 12000 khz
    X, sr = librosa.load(file_name, sr=sr, mono=True, offset=offset, duration=duration)
    if X.shape[0] > segment_length:
        X = X[:segment_length]
    return X

> NOTE: To try out your own song, simply place it in the example_songs directory in the notebooks folder, and replace `get-you.mp3` with your song name.

In [21]:
song_path = os.path.join(os.getcwd(), 'example_songs', 'get-you.mp3') # <- Replace this to try out your own song!!
song_samples = extract_samples(song_path, offset=120.0)
song_samples.shape = (1, len(song_samples), 1)

## Step 2. Load the Model

Now that we have our song, let's load a model. <br/>

In [6]:
model = keras.models.load_model(os.path.join(os.pardir, 'pretrained', 'SampleCNN_KAIST_31104_12khz_off57.h5'))

Now let's feed our samples into the model and make a prediction! <br />

## Step 3. Predict!

In [13]:
mood_values = model.predict(song_samples)
print('Mood Values: ', {'Angry': mood_values[0][0], 'Happy': mood_values[0][1], 'Sad': mood_values[0][2], 'Romantic': mood_values[0][3]})

Mood Values:  {'Angry': 8.623318e-07, 'Happy': 7.0832094e-08, 'Sad': 3.256653e-08, 'Romantic': 0.9999989}


Cool our prediction is made! Now we have a value for each mood. Let's take the max value to see what our model thought the strongest mood was, and print in English the mood that it corresponds to. <br />
We'll do this in a function, so we can reuse it on other songs.

In [16]:
def get_label_from_mood_values(song_path, mood_values):
    song_name = ''.join(song_path.split('\\')[-1:])
    prediction_string =''
    # prediction_string = 'Mood values: {}\n'.format(str(mood_values) + '\n')
    mood_prediction = np.argmax(mood_values)
    if mood_prediction == 0:
        prediction_string += '{} is predicted to be: {}'.format(song_name, 'angry >:(')
    elif mood_prediction == 1:
        prediction_string += '{} is predicted to be: {}'.format(song_name, 'happy :)')
    elif mood_prediction == 2:
        prediction_string += '{} is predicted to be: {}'.format(song_name, 'sad :(')
    elif mood_prediction == 3:
        prediction_string += '{} is predicted to be: {}'.format(song_name, 'romantic <3')
    return prediction_string

In [19]:
prediction_label = get_label_from_mood_values(song_path, mood_values)
display(Markdown('<h2>{}</h2>'.format(prediction_label.split('/')[-1])))

<h2>get-you.mp3 is predicted to be: romantic <3</h2>

#### *How do you think this song feels?*

In [10]:
IPython.display.Audio(song_path)